In [105]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

webpage = requests.get('https://www.beeradvocate.com/beer/top-rated/')

In [106]:
product_name = []
product_review = []
user_rating = []

In [107]:
webpage

<Response [200]>

In [108]:
BeautifulSoup(webpage.content)

<!DOCTYPE html>
<html class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar Responsive pageIsLtr not_hasTabLinks not_hasSearch is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" dir="LTR" id="XenForo" lang="en-US" xmlns:fb="http://www.facebook.com/2008/fbml">
<head>
<meta charset="utf-8"/>
<meta content="IE=Edge,chrome=1" http-equiv="X-UA-Compatible"/>
<meta content="width=device-width, initial-scale=1" name="viewport"/>
<base href="https://www.beeradvocate.com/community/"/>
<script>
			var _b = document.getElementsByTagName('base')[0], _bH = "https://www.beeradvocate.com/community/";
			if (_b && _b.href != _bH) _b.href = _bH;
		</script>
<title>Top 250 Rated Beers | BeerAdvocate</title>
<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>
<link href="css.php?css=xenforo,form,public&amp;style=6&amp;dir=LTR&amp;d=1694879621" rel="stylesheet"/>
<link href="css.php?css=login_bar,moderator_bar,notices,panel_scroller,uix_exten

In [109]:
#links = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)
#links

# Find the anchor tag within the <td> element
anchor_tag = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)
anchor_tag


[<a href="/beer/profile/23222/78820/"><b>Kentucky Brunch Brand Stout</b></a>,
 <a href="/beer/profile/23222/">Toppling Goliath Brewing Company</a>,
 <a href="/beer/profile/23222/113831/"><b>Vanilla Bean Assassin</b></a>,
 <a href="/beer/profile/23222/">Toppling Goliath Brewing Company</a>,
 <a href="/beer/profile/26/42349/"><b>Marshmallow Handjee</b></a>,
 <a href="/beer/profile/26/">3 Floyds Brewing Co.</a>,
 <a href="/beer/profile/25888/87246/"><b>Abraxas - Barrel-Aged</b></a>,
 <a href="/beer/profile/25888/">Perennial Artisan Ales</a>,
 <a href="/beer/profile/17981/110635/"><b>Hunahpu's Imperial Stout - Double Barrel Aged</b></a>,
 <a href="/beer/profile/17981/">Cigar City Brewing</a>,
 <a href="/beer/profile/24903/486325/"><b>Blessed</b></a>,
 <a href="/beer/profile/24903/">Anchorage Brewing Company</a>,
 <a href="/beer/profile/46317/16814/"><b>Heady Topper</b></a>,
 <a href="/beer/profile/46317/">The Alchemist</a>,
 <a href="/beer/profile/32319/348026/"><b>O.W.K.</b></a>,
 <a href

In [110]:
link = anchor_tag[0].get('href')
link

'/beer/profile/23222/78820/'

In [111]:
product_list = 'https://www.beeradvocate.com'+ link
product_list

'https://www.beeradvocate.com/beer/profile/23222/78820/'

In [112]:
new_webpage = requests.get(product_list)
new_webpage

<Response [200]>

In [113]:
new_soup = BeautifulSoup(new_webpage.content)
new_soup

<!DOCTYPE html>
<html class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar Responsive pageIsLtr not_hasTabLinks not_hasSearch is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" dir="LTR" id="XenForo" lang="en-US" xmlns:fb="http://www.facebook.com/2008/fbml">
<head>
<meta charset="utf-8"/>
<meta content="IE=Edge,chrome=1" http-equiv="X-UA-Compatible"/>
<meta content="width=device-width, initial-scale=1" name="viewport"/>
<base href="https://www.beeradvocate.com/community/"/>
<script>
			var _b = document.getElementsByTagName('base')[0], _bH = "https://www.beeradvocate.com/community/";
			if (_b && _b.href != _bH) _b.href = _bH;
		</script>
<title>Kentucky Brunch Brand Stout | Toppling Goliath Brewing Company | BeerAdvocate</title>
<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>
<link href="css.php?css=xenforo,form,public&amp;style=6&amp;dir=LTR&amp;d=1694879621" rel="stylesheet"/>
<link href="css.php?css=login_bar,mod

#### Find title

In [76]:
title_div = new_soup.find("div", class_="titleBar")
h1_tag = title_div.find("h1")

# Remove the text from any child elements within the <h1> tag
for elem in h1_tag.find_all():
    elem.extract()

# Extract and print the cleaned text within the <h1> tag
title_text = h1_tag.get_text(strip=True)
print(title_text)

Kentucky Brunch Brand Stout


#### Find review

In [118]:
div_with_text = new_soup.findall('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')

desired_text = div_with_text.get_text(strip=True)
print(desired_text)

AttributeError: ResultSet object has no attribute 'get_text'. You're probably treating a list of elements like a single element. Did you call find_all() when you meant to call find()?

#### Find user rating

In [84]:
# Attempt to find the rating within <span class="BAscore_norm">
rating_span = new_soup.find('span', class_='BAscore_norm')

if rating_span:
    rating = rating_span.text
else:
    # If not found, look for the rating within <span class="muted">
    rating_span_muted = new_soup.find('span', class_='muted')
    if rating_span_muted:
        rating_start = "Rated: <b>"
        rating_end = "</b>"
        rating_text = rating_span_muted.get_text(strip=True)
        
        # Find the start and end positions of the rating
        start_pos = rating_text.find(rating_start)
        end_pos = rating_text.find(rating_end, start_pos + len(rating_start))
        
        if start_pos != -1 and end_pos != -1:
            rating = rating_text[start_pos + len(rating_start):end_pos]
        else:
            rating = "Rating not found"
    else:
        rating = "Rating not found"

print("Rating:", rating)

Rating: 5


# Gathers all the links

In [177]:
import requests
from bs4 import BeautifulSoup
import re
import time

# Function to scrape the links
def scrape_links(url):
    response = requests.get(url)
    if response.status_code == 200:
        soup = BeautifulSoup(response.text, 'html.parser')
        anchor_tags = soup.find_all('a', href=lambda href: href and re.match(r'/beer/profile/\w+/\w+', href))
        links_list = [tag.get('href') for tag in anchor_tags]
        return links_list
    else:
        print(f"Failed to retrieve content from {url}. Status code: {response.status_code}")
        return []

# Define the base URL
base_url = 'https://www.beeradvocate.com'

# Specify the initial URL to scrape
initial_url = 'https://www.beeradvocate.com/beer/top-styles/157/'

# Scrape the links from the initial URL
links_list = scrape_links(initial_url)

# Iterate through the links and make requests
for link in links_list:
    product_list = base_url + link
    new_webpage = requests.get(product_list)
    
    if new_webpage.status_code == 200:
        # Process the content of the new_webpage as needed
        # For example, print the URL and content
        print(f"URL: {product_list}")
        print("Content:")
        print(new_webpage.content)  # You can also process or parse the content here
    else:
        print(f"Failed to retrieve content from {product_list}. Status code: {new_webpage.status_code}")

    # Add a delay of 1 second between requests to avoid overloading the server
    time.sleep(1)


URL: https://www.beeradvocate.com/beer/profile/23222/78820/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Kentucky Brunch Brand Stout | Toppling Goliath Brewing Company | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?c

URL: https://www.beeradvocate.com/beer/profile/23222/113831/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Vanilla Bean Assassin | Toppling Goliath Brewing Company | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?css=xe

URL: https://www.beeradvocate.com/beer/profile/32319/348026/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>O.W.K. | Side Project Brewing | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?css=xenforo,form,public&amp;style

URL: https://www.beeradvocate.com/beer/profile/25888/87246/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Abraxas - Barrel-Aged | Perennial Artisan Ales | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?css=xenforo,form,

URL: https://www.beeradvocate.com/beer/profile/24903/486325/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Blessed | Anchorage Brewing Company | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?css=xenforo,form,public&amp

...

URL: https://www.beeradvocate.com/beer/profile/17981/54647/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Hunahpu\'s Imperial Stout - Bourbon Barrel-Aged | Cigar City Brewing | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css

URL: https://www.beeradvocate.com/beer/profile/28743/531838/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Brownie | Tree House Brewing Company | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?css=xenforo,form,public&am

URL: https://www.beeradvocate.com/beer/profile/1146/563022/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Bourbon County Double Barrel Toasted Barrel Stout | Goose Island Beer Co. | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href

URL: https://www.beeradvocate.com/beer/profile/24445/75343/
Content:
b'<!DOCTYPE html>\n<html id="XenForo" lang="en-US" dir="LTR" class="Public NoJs uix_javascriptNeedsInit LoggedOut Sidebar  Responsive pageIsLtr   not_hasTabLinks  not_hasSearch   is-sidebarOpen hasRightSidebar is-setWidth navStyle_0 pageStyle_0 hasFlexbox" xmlns:fb="http://www.facebook.com/2008/fbml">\n<head>\n<meta charset="utf-8" />\n<meta http-equiv="X-UA-Compatible" content="IE=Edge,chrome=1" />\n<meta name="viewport" content="width=device-width, initial-scale=1" />\n<base href="https://www.beeradvocate.com/community/" />\n<script>\n\t\t\tvar _b = document.getElementsByTagName(\'base\')[0], _bH = "https://www.beeradvocate.com/community/";\n\t\t\tif (_b && _b.href != _bH) _b.href = _bH;\n\t\t</script>\n<title>Clare\'s Thirsty Ale | Haymarket Beer Co. Pub & Brewery | BeerAdvocate</title>\n<noscript><style>.JsOnly, .jsOnly { display: none !important; }</style></noscript>\n<link rel="stylesheet" href="css.php?css=xenf

KeyboardInterrupt: 

In [89]:
import requests
from bs4 import BeautifulSoup
import re
import time
import pandas as pd

# Function to scrape the links
def scrape_links(url):
    response = requests.get(url)
    if response.status_code == 200:
        soup = BeautifulSoup(response.text, 'html.parser')
        anchor_tags = soup.find_all('a', href=lambda href: href and re.match(r'/beer/profile/\w+/\w+', href))
        links_list = [tag.get('href') for tag in anchor_tags]
        return links_list
    else:
        print(f"Failed to retrieve content from {url}. Status code: {response.status_code}")
        return []

# Define the base URL
base_url = 'https://www.beeradvocate.com'

# Specify the initial URL to scrape
initial_url = 'https://www.beeradvocate.com/beer/top-styles/157/'

# Scrape the links from the initial URL
links_list = scrape_links(initial_url)

# Create an empty DataFrame to store the extracted information
data = []

# Iterate through the links and make requests
for link in links_list:
    product_list = base_url + link
    new_webpage = requests.get(product_list)
    
    if new_webpage.status_code == 200:
        new_soup = BeautifulSoup(new_webpage.content, 'html.parser')
        
        # Extract the title
        title_div = new_soup.find("div", class_="titleBar")
        h1_tag = title_div.find("h1")
        for elem in h1_tag.find_all():
            elem.extract()
        title_text = h1_tag.get_text(strip=True)
        
        # Extract the review
        div_with_text = new_soup.find('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')
        desired_text = div_with_text.get_text(strip=True)
        
        # Extract the rating
        rating_span = new_soup.find('span', class_='BAscore_norm')
        if rating_span:
            rating = rating_span.text
        else:
            rating_span_muted = new_soup.find('span', class_='muted')
            if rating_span_muted:
                rating_start = "Rated: <b>"
                rating_end = "</b>"
                rating_text = rating_span_muted.get_text(strip=True)
                start_pos = rating_text.find(rating_start)
                end_pos = rating_text.find(rating_end, start_pos + len(rating_start))
                if start_pos != -1 and end_pos != -1:
                    rating = rating_text[start_pos + len(rating_start):end_pos]
                else:
                    rating = "Rating not found"
            else:
                rating = "Rating not found"
        
        # Add the extracted information to the data list
        data.append({'Title': title_text, 'Review': desired_text, 'Rating': rating})
        
        # Print or process the content of the new_webpage here
        print(f"URL: {product_list}")
        print("Title:", title_text)
        print("Review:", desired_text)
        print("Rating:", rating)
    else:
        print(f"Failed to retrieve content from {product_list}. Status code: {new_webpage.status_code}")

    # Add a delay of 1 second between requests to avoid overloading the server
    time.sleep(1)

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Print the DataFrame
print(df)


URL: https://www.beeradvocate.com/beer/profile/23222/78820/
Title: Kentucky Brunch Brand Stout
Review: Amazing stout, expensive but worth the price!
Rating: 5
URL: https://www.beeradvocate.com/beer/profile/23222/113831/
Title: Vanilla Bean Assassin
Review: 12oz bottle…2022 version. Drank 12/25/22.Pours dark brown/black, not much carbonation. Smells of sweet chocolate, vanilla, and barrel. Taste is marshmallows soaked in bourbon. Perfect sweetness. If there is a knock it’s slightly on the thin side, but that’s being picky. Probably the best adjunct stout I’ve had. Truly lives up to the hype.
Rating: 4.86
URL: https://www.beeradvocate.com/beer/profile/32319/348026/
Title: O.W.K.
Review: B2. Served at SP from bottle. Waited for it to warm for awhile. Pitch black. Nice balance of bourbon and vanilla on the nose. Complex beer. Starts off with bourbon forward, then vanilla comes in very subtlety and finishes with delicious chocolate. Medium to heavy mouthfeel. Would’ve liked it heavier some.

URL: https://www.beeradvocate.com/beer/profile/1199/19960/
Title: KBS
Review: Looks: Beautiful, tan, creamy head over dark brown beer.Smell: Coffee, bourbon, alcohol, just a little subduedTaste: This is not subtle. Sweet without being sugary. Bourbon, coffee, chocolate and some alcohol. More balanced than something like Dragon’s Milk that is a little too sugary.Feel: Thick and just a little effervescent.Overall: Yum. My favorite stout, I think.
Rating: 4.77
URL: https://www.beeradvocate.com/beer/profile/1146/10672/
Title: Bourbon County Brand Stout
Review: Goose Island Bourbon County imperial stout.Now I must say, this is quite quite good. Like very good. Somewhere between a good stout and an aged whiskey, which isn't a surprise based on the drink itself. That being said, it does not exemplify the thing I like most about beer so far being, drinkability. I do like the refreshing nature of a beer quite a bit and that is the only thing I'd say is absent here.At 14.3 percent, it's quite hi

URL: https://www.beeradvocate.com/beer/profile/16866/51257/
Title: Black Tuesday
Review: Well, this will definitely get you lit. If you want a clean, bourbon forward stout then look no further. The barrel is over the top but still under control, which makes for an exquisite tasting experience.
Rating: 4.07
URL: https://www.beeradvocate.com/beer/profile/33824/231652/
Title: Fundamental Forces
Review: 100 rating like George Burnes on a cigar, here we go. Large and in charge like Veronica lake after a Martin or three, let’s ride. More solid than Robert Taylor as Ivanhoe, god save the king.
Rating: 4.25
URL: https://www.beeradvocate.com/beer/profile/31987/319512/
Title: Modem Tones - Bourbon Barrel-Aged - Vanilla
Review: 12oz can courtesy of Dimidiata. Been sitting on it for a bit, and decided it would be an excellent Valentine for myself.Poured into a snifter, it was the color of the mood of Philadelphia Eagles fans right now. Virtually no head besides a very thin line of tan bubbles arou

URL: https://www.beeradvocate.com/beer/profile/30654/325511/
Title: Affogato - Bourbon Barrel-Aged
Review: Whale huntingBrewers Notes: Collaboration with J. Wakefield BrewingWe took our original J. Wakefield collaboration Affogato Imperial Stout and aged it in bourbon barrels for 6 months at our Hudson Road barrel house. Affogato Imperial Stout is inspired by a few of our brewers' favorite summertime pick-me-up (& cool-me-down) Barrington's affogato.Barrel Aged Affogato Imperial Stout is decadent, rich and full. Brewed with a blend of Barrington & Mostra beans, Affogato leads with aromas of vanilla, toasted marshmallows and subtle notes of bourbon. Barrel Aged Affogato has a full, satisfying body and an indulgent palate of vanilla cream, hot cocoa, rich brownie batter, with complimentary doses of smooth coffee and bourbon.MALT: American 2-Row Barley, Crystal 120, Flaked Oats, Black Malt, Chocolate Malt, Munich Malt, White Wheat Malt, Brown Sugar, Dark Candied Syrup, LactoseHOPS, ETC: C

URL: https://www.beeradvocate.com/beer/profile/28743/531838/
Title: Brownie
Review: This one pours a fairly dark black color, with a small head, and a little bit of lacing.This smells like chocolate fudge, roasty coffee, vanilla, oak, and bourbon.This was much better than I thought it would be, honestly. There's a great dark and fudgy chocolate character to it. There's a touch of coffee, but it's mostly a wonderful chocolate character here. There's a spicy oak character, and some nice bourbon tones, with very little booze on this. It's clearly very well blended.This is thick, smooth, and chewy, with a nice drinkability.This is highly impressive stuff - I need to find more of TH's barrel program, clearly.
Rating: 4.43
URL: https://www.beeradvocate.com/beer/profile/1146/563022/
Title: Bourbon County Double Barrel Toasted Barrel Stout
Review: 500 ml bottle into a snifter. Bottled 7/20/21, had 3/12/22.Pours an opaque dark brown, with a quarter inch quickly dissipating head and some spotty 

URL: https://www.beeradvocate.com/beer/profile/49747/320038/
Title: Henna: S’more
Review: #151, sweet and delicious
Rating: 4.9
URL: https://www.beeradvocate.com/beer/profile/2210/95028/
Title: PNC Imperial Buckwheat Stout
Review: 2013 at Toronado in 2014
Rating: 5
URL: https://www.beeradvocate.com/beer/profile/33824/120155/
Title: Leche Borracho
Review: #178, good stuff!
Rating: 4.9
URL: https://www.beeradvocate.com/beer/profile/2097/123872/
Title: Solstice Stout
Review: 2022 vintage, poured at fridge temp. Pours jet black with basically no head. The nose is crazy. Huge roasted malts, black licorice, sticky toffee, vanilla, maple, and loads of dark fruit. Lovely.The taste is really nice. Maple syrup, roasted malts, vanilla, licorice, toffee, bitter oak, cherries, blackberries, prunes, and some coffee grounds. Super intense.Mouthfeel is pretty thick and viscous. The aftertaste is bitter malts and sticky toffee.
Rating: 4.21
URL: https://www.beeradvocate.com/beer/profile/16866/132291/
T

URL: https://www.beeradvocate.com/beer/profile/23222/521539/
Title: Term Oil Fluffernutter
Review: 5oz draft pour in a snifter. heavy peanut butter aroma with a tinge of marshmallow / vanilla and not much barrel. taste follows with a little bit of barrel sting on the finish. definitely peanut forward but with some chocolate from the base stout. thick, heavy mouthfeel. good stuff!
Rating: 4.44
URL: https://www.beeradvocate.com/beer/profile/33824/333734/
Title: Paisley Cave Complex
Review: 08/12/23 bottle @ home
Rating: 4.75
URL: https://www.beeradvocate.com/beer/profile/28743/526719/
Title: Persist
Review: 12 oz bottle poured into a snifter. Pours an oily jet black with a thin tan head. Some lacing, and tons of sediment at the bottom of the bottle (most of which went down the drain, not into my glass). Aroma and flavor feature sweet maple, vanilla, coffee, oak, bourbon, and dark roasted malts. It's quite sweet but not cloying. Hides the abv extremely well. Mouthfeel has light carbonatio

In [97]:
import requests
from bs4 import BeautifulSoup
import time
import pandas as pd

# Function to scrape all reviews and ratings
def scrape_reviews_and_ratings(url):
    response = requests.get(url)
    if response.status_code == 200:
        soup = BeautifulSoup(response.content, 'html.parser')
        
        # Extract the title
        title_div = soup.find("div", class_="titleBar")
        h1_tag = title_div.find("h1")
        for elem in h1_tag.find_all():
            elem.extract()
        title_text = h1_tag.get_text(strip=True)
        
        # Find all the review divs
        review_divs = soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')
        
        # Initialize lists to store reviews and ratings
        reviews = []
        ratings = []
        
        for review_div in review_divs:
            # Extract review text if available
            div_with_text = review_div.find('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')
            review_text = div_with_text.get_text(strip=True) if div_with_text else ""
            
            # Extract rating
            rating_span = review_div.find('span', class_='BAscore_norm')
            if rating_span:
                rating = rating_span.text
            else:
                rating_span_muted = review_div.find('span', class_='muted')
                if rating_span_muted:
                    rating_start = "Rated: <b>"
                    rating_end = "</b>"
                    rating_text = rating_span_muted.get_text(strip=True)
                    start_pos = rating_text.find(rating_start)
                    end_pos = rating_text.find(rating_end, start_pos + len(rating_start))
                    if start_pos != -1 and end_pos != -1:
                        rating = rating_text[start_pos + len(rating_start):end_pos]
                    else:
                        rating = "Rating not found"
                else:
                    rating = "Rating not found"
            
            # Append review and rating to their respective lists
            reviews.append(review_text)
            ratings.append(rating)
        
        # Return the title, reviews, and ratings as a dictionary
        return {'Title': title_text, 'Reviews': reviews, 'Ratings': ratings}
    
    else:
        print(f"Failed to retrieve content from {url}. Status code: {response.status_code}")
        return None

# Define the base URL
base_url = 'https://www.beeradvocate.com'

# Specify the initial URL to scrape
initial_url = 'https://www.beeradvocate.com/beer/top-styles/157/'

# Scrape the links from the initial URL
links_list = scrape_links(initial_url)

# Create an empty list to store the extracted information
data = []

# Iterate through the links and make requests
for link in links_list:
    product_list = base_url + link
    result = scrape_reviews_and_ratings(product_list)
    
    if result:
        # Append the result to the data list
        data.append(result)
        
        # Print or process the content of the new_webpage here
        print(f"URL: {product_list}")
        print("Title:", result['Title'])
        print("Number of Reviews:", len(result['Reviews']))
        print("Ratings:", result['Ratings'])
    else:
        print(f"Failed to retrieve content from {product_list}.")
    
    # Add a delay of 1 second between requests to avoid overloading the server
    time.sleep(1)

# Create a DataFrame from the extracted data
df = pd.DataFrame(data)

# Print the DataFrame
#print(df)


URL: https://www.beeradvocate.com/beer/profile/23222/78820/
Title: Kentucky Brunch Brand Stout
Number of Reviews: 5
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/23222/113831/
Title: Vanilla Bean Assassin
Number of Reviews: 1
Ratings: ['Rating not found']
URL: https://www.beeradvocate.com/beer/profile/32319/348026/
Title: O.W.K.
Number of Reviews: 1
Ratings: ['Rating not found']
URL: https://www.beeradvocate.com/beer/profile/25888/87246/
Title: Abraxas - Barrel-Aged
Number of Reviews: 4
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/24903/486325/
Title: Blessed
Number of Reviews: 9
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.bee

URL: https://www.beeradvocate.com/beer/profile/28743/113784/
Title: Double Shot
Number of Reviews: 8
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/33824/568763/
Title: Deprecophobia
Number of Reviews: 8
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/396/31484/
Title: Speedway Stout - Bourbon Barrel-Aged
Number of Reviews: 9
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/38773/497046/
Title: Medianoche - Coconut Coffee
Number of Reviews: 6
Ratings: ['Rating not foun

URL: https://www.beeradvocate.com/beer/profile/30356/258280/
Title: Barrel Aged Christmas Bomb!
Number of Reviews: 1
Ratings: ['Rating not found']
URL: https://www.beeradvocate.com/beer/profile/16866/109989/
Title: Mocha Wednesday
Number of Reviews: 4
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/49747/320038/
Title: Henna: S’more
Number of Reviews: 2
Ratings: ['Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/2210/95028/
Title: PNC Imperial Buckwheat Stout
Number of Reviews: 7
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profile/33824/120155/
Title: Leche Borracho
Number of Reviews: 4
Ratings: ['Rating not found', 'Rating not found', 'Rating not found', 'Rating not found']
URL: https://www.beeradvocate.com/beer/profil

# Gathers all the reviews

In [210]:
import requests
from bs4 import BeautifulSoup

webpage = requests.get('https://www.beeradvocate.com/beer/top-rated/')
soup = BeautifulSoup(webpage.content, 'html.parser')
anchor_tag = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)
link = anchor_tag[0].get('href')
product_list = 'https://www.beeradvocate.com'+ link
new_webpage = requests.get(product_list)
new_soup = BeautifulSoup(new_webpage.content)
div_with_text = new_soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')

desired_text = [div.get_text(strip=True) for div in div_with_text]

for text in desired_text:
    print(text)


Amazing stout, expensive but worth the price!
This beer meet and exceeded all the unreal hype. It is simply amazing!
Let it sit and warm to the room a little ... unbelievable.
A small pour, ebony dark, no real head. Intense, rich aroma, brownies and German chocolate cake; dark sweetness. The taste amplifies the smell with the addition of sublime Kentucky bourbon. Heavy body; dense, chewy residual sugar feel with a sublime whiskey heat.This beauty was generously provided by @azuelke (Adam) at a bottle share hosted by @GreenBayBA in Sheboygan, WI. There were many great beers sample, many beautiful and exquisite dark beers, but nothing quite like this legendary beer. If ever you have a chance to try this one, all I can say is don't pass it up. The beer lives up to its legendary status.Pouring temperature: n/a; bottling info: unknown year, bottle number #138Source: @azuelke (Adam), Sheboygan, WI bottle share
Vintage 2022, served on tap at Toppling Goliath in a "snulip" glass. Opaque deep b

In [212]:
import requests
from bs4 import BeautifulSoup

# Define the base URL
base_url = 'https://www.beeradvocate.com/beer/top-rated/'

# Send a request to the base URL and parse the content
webpage = requests.get(base_url)
soup = BeautifulSoup(webpage.content, 'html.parser')

# Find all anchor tags with 'href' containing '/beer/profile/'
anchor_tags = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)

# Iterate through the links and extract desired information
for anchor_tag in anchor_tags:
    link = anchor_tag.get('href')
    product_list_url = 'https://www.beeradvocate.com' + link

    # Send a request to the linked page and parse the content
    new_webpage = requests.get(product_list_url)
    new_soup = BeautifulSoup(new_webpage.content, 'html.parser')

    # Find the div with the specified style attribute
    div_with_text = new_soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')

    # Extract and print the desired text
    desired_text = [div.get_text(strip=True) for div in div_with_text]
    for text in desired_text:
        print(text)


Amazing stout, expensive but worth the price!
This beer meet and exceeded all the unreal hype. It is simply amazing!
Let it sit and warm to the room a little ... unbelievable.
A small pour, ebony dark, no real head. Intense, rich aroma, brownies and German chocolate cake; dark sweetness. The taste amplifies the smell with the addition of sublime Kentucky bourbon. Heavy body; dense, chewy residual sugar feel with a sublime whiskey heat.This beauty was generously provided by @azuelke (Adam) at a bottle share hosted by @GreenBayBA in Sheboygan, WI. There were many great beers sample, many beautiful and exquisite dark beers, but nothing quite like this legendary beer. If ever you have a chance to try this one, all I can say is don't pass it up. The beer lives up to its legendary status.Pouring temperature: n/a; bottling info: unknown year, bottle number #138Source: @azuelke (Adam), Sheboygan, WI bottle share
Vintage 2022, served on tap at Toppling Goliath in a "snulip" glass. Opaque deep b

For me this is the GOAT. Don’t want to repeat what has already been said, but it just has an unbelievable balance and a je ne sais quoi that is extremely satisfying to enjoy. A beer that elevates the experience from a tasty beverage to something to transform the simple act of drinking into something more thought provoking. Also, for me it is much more balanced than Focal, which some prefer. Cheers.
Poured from a 16 ounce can dated 7-31-23 into a teku glass.Look- Medium gold, very hazy, frothy white head, above average head retention and lacing.Smell- Pine resin, clementine, nectarine, dank, earthy, medium strength of scent.Taste- Pine resin, clementine, pithy, pineapple, herbaceous, high strength of flavor.Feel- Between medium and full body, average carbonation, highly creamy, moderately bitter, mildly mouth warming, mildly dry finish.Overall- Medium gold and very hazy with above average head retention and lacing. Bouquet was medium strength with notes of pine resin, clementine, nectar

2021 batch 3, drank in June 2022. Didn't get as much from this as previous ADWTD. Felt sweet without complexity that you would expect. Still very delicious, just not worth the price.
Complex and boozy, hits all the right barley wine notes but adds so much more. Fruity, sweet but not cloying. Thick but not too heavy, just all around outstanding.
My first sacrifice at Dark Lord Day 2023 (it's back baby!!!), this screenprinted batch 1 Triple Oak label--sporting those the Aussie stickers with pride--poured a mildly viscous clear reddish-copper with nary a head to speak of, though ringed by a bubbly tan chain.Intensely woody up front, it even leans a little pungent and catty right out of the bottle. However, it quickly transforms into an explodingly delectable maple tempered by a whiskey heat that both continue to expand on the exhale and with each subsequent sip.Though this definitely shows its age, it's quite the experience nevertheless. Still, I'm not sure anything can beat my nostalgia 

Intense gummy bear nose. Taste is soft stone fruit, green pear, grapefruit rind, and an absolute blast of pine resin. Prickly mouthfeel. Dry, bitter finish. Phenomenal.
Perfect.Boozy, be careful
I've been chasing this beer for the better part of 13 years. Today was finally the day. 500ml capped bottle into a Fuzzy IPA glass.Pours crystal clear goldenrod with a slowly building 2 finger foamy white head that sits around. Patchy, stringy lace sticks to the inside of the glass. Nose is citrus, pine, grass, and sap. Fresh, aggressive, resiny. Very pungent. Beer opens grass, pine, and citrus. Zesty towards the middle with loads of fresh pine, unripened tropical fruit, and tree sap. Finishes with a crystal clean bitterness that is dry and lingers in the aftertaste. Body is light to medium with ample carbonation. Prickly and lively on the palate, and goes down dry with a lingering, sticky aftertaste.I may be buying into the hype a bit after all this time but in a category that everyone in the 

Quite certain I've had this one before, but apparently never reviewed. Yeah, it's decent! I lack the flair with my superlatives these days to detail the nuances. If you can get your hands on this one, do so.
Pours like opaque guava juice with a 2 finger creamy off-white head that faded extremely slowly and left really nice lacing on the glass. It smells like tangerine, orange juice, papaya, tropical fruit, dank citrus hops, faint biscuit, a hint of caramel and some flowery spices as it fades. The flavor was very similar to the nose with tangerine, orange juice, papaya, tropical fruit, and the additions of peaches, lemon zest and citrus hops that have off the dry hopped vibe. More malty backbone in the taste with sweet grains, biscuit, chalky yeast, graham cracker and then spices like coriander or white pepper in the finish. The bitterness level was perfect and the taste completely hid the ABV, this indeed was very hazy and very tasty overall.
4/30/23 Canned 4/19/22. What more could you

...

Solid beer - a bit plum tart aftertaste.
Original bottlingIt is a clear, reddish plum pour with half a finger of pure white head. It looks less thick than many of the HF saisons I have tried, but "prettier".Tart plum bursts from the bottle and fills the room. As I pour it gets even stronger. My salivary glands fire before I even put nose to glass. Such a delicious aroma, it calls, entices, with fresh plum, tart sourdough, raspberry jam, grape must notes, honeysuckle, hints of spicy alcohol and fresh flowers, in perfect balance to create a stunning aroma.All the flavors of the nose are here, no need to repeat them, balanced perfectly, in a wonderful blend. It ends a lightly jammy whih fades into a tart, fruity linger. As it warms hints of an herbal bitterness enter the mix, quite lightly, and it gets even better.Medium body for style, light carbonation which works well here, clean as a whistle, with a brilliantly flavored linger that is just right to bring on desire for next sip.Another

Always love when I get a chance to drink some Hill Farmstead and as usual, it did not disappoint. Soft with great aroma and flavour from the hops that was easy drinking and went down way too fast.
Can from Jeff, thanks for the hookup!Hazy bright lemon orange color with a thin white head that slowly dissipates. Tropical orange and bits of pine and grass. sweet bready backbone. Pretty nice beer.
16oz can dated 9/8/22.Pours clear gold with a chill haze and a half-inch head. Retention and lacing is moderate. Grape and peach in the nose. Aromatics are unexpectedly subdued. Medium bodied with a crisp, almost tacky mouthfeel. White grape, dank resin, and faint garlic on the palate. Finishes with a firm bitterness, light malt, and lingering dank grape must.
On tap at Armsby Abby.L -- Golden orange with the usual HF fluffy, sticky, white headS -- What a lovely showcase of Galaxy. Not too sweaty/oniony, just tons of tropical fruit, creamy citrus flesh, and sweet floral. Doesn't pop out of the gl

Explosive grapefruit nose after popping the top. Orange-yellow hazy pour with a loose bubbly head. Really nice evolution of flavors from opening with orange, then tropical fruit followed by a nice grapefruit T-Rex bite for the finish. Can't wait to get bitten again.
Good a little spicy a little grapefruit. Would do again.
Picked up a four-pack from the Appalachian Vintner 6-21-23 for $18.49. Canned 5-26-23; consumed can #1& 2 6-22-23.Beer poured a hazy light golden orange with an okay white head.Nose is very nice, citrus and tropical fruit forward.Taste is a light but substantive pale malt base that allows the hops to shine thru and that they do. Very flavorful with orange, papaya, and mango shining through. Finishes with a touch of grapefruit and some major pith; 7/10 on my bitterness scale.Mouthfeel is ultra-light and very refreshing.Overall, yep, King Sue lives up to its reputation!
While I wanted more coconut up front, this was an amazingly complex beer everywhere else; phenomenal 

From a 500ml bottle, dated 03/11/23. Served in a spiegelau tulip glass.Pours a thin-appearing oak-brown with no obvious highlights. A generous finger of lush, coffee colored foam doesn’t last but maybe 20 seconds leaving a narrow collar and a rousable spatter of oily, super-slippery lacing.Nose is… fruity? A sweet, candy-like coffee aroma and, totally unexpectedly, raspberry - which must be an olfactory hallucination, or at least how my brain is interpreting the combination of vanilla, cinnamon and chiles.Taste is sweet but not heavily so, with a berry-like coffee bean flavour and that fruity mélange of cinnamon-vanilla-chile pepper that my brain persists in translating as ‘raspberry’ bringing a brightness and lightness which keeps the beer from tasting syrupy. A slick Cadbury-like milk chocolatey character becomes more evident as the beer warms accompanied by some heat from the chiles. There’s a very faint soy sauce quality in the aftertaste which doesn’t detract much.Feel is oily-smo

KeyboardInterrupt: 

# Gather all the ratings

In [175]:
rating_div = new_soup.find_all('span', class_='BAscore_norm')
rating_div

[<span class="BAscore_norm">5</span>,
 <span class="BAscore_norm">5</span>,
 <span class="BAscore_norm">5</span>,
 <span class="BAscore_norm">4.67</span>,
 <span class="BAscore_norm">5</span>]

In [176]:
import re

# Find all elements with the specified class
rating_div = new_soup.find_all('span', class_='BAscore_norm')

# Define the regular expression pattern to extract ratings
pattern_decimal = r'<span class="BAscore_norm">(\d+\.\d+)</span>'
pattern_integer = r'<span class="BAscore_norm">(\d+)</span>'

# Initialize a list to store the extracted ratings
ratings_list = []

# Loop through each rating_div and extract ratings using re.findall
for rating_d in rating_div:
    ratings_decimal = re.findall(pattern_decimal, str(rating_d))
    ratings_integer = re.findall(pattern_integer, str(rating_d))
    
    # Extend the ratings_list with both decimal and integer ratings
    ratings_list.extend(ratings_decimal)
    ratings_list.extend(ratings_integer)

# Print the list of extracted ratings
for i, rating in enumerate(ratings_list, start=1):
    print(f"Rating {i}: {rating}")


Rating 1: 5
Rating 2: 5
Rating 3: 5
Rating 4: 4.67
Rating 5: 5


In [172]:
import re

# Find all elements with the specified class
rating_divs = new_soup.find_all('span', class_='muted')

# Define the regular expression pattern to extract ratings
pattern_decimal = r'<b>(\d+\.\d+)</b>'
pattern_integer = r'<b>(\d+)</b>'

# Initialize a list to store the extracted ratings
ratings_list = []

# Loop through each rating_div and extract ratings using re.findall
for rating_div in rating_divs:
    ratings_decimal = re.findall(pattern_decimal, str(rating_div))
    ratings_integer = re.findall(pattern_integer, str(rating_div))
    
    # Extend the ratings_list with both decimal and integer ratings
    ratings_list.extend(ratings_decimal)
    ratings_list.extend(ratings_integer)

# Print the list of extracted ratings
for i, rating in enumerate(ratings_list, start=1):
    print(f"Rating {i}: {rating}")


Rating 1: 4.75
Rating 2: 4.52
Rating 3: 5
Rating 4: 5
Rating 5: 4.96
Rating 6: 4.5
Rating 7: 4.75
Rating 8: 4.75
Rating 9: 5
Rating 10: 4.78
Rating 11: 4.84
Rating 12: 4.69
Rating 13: 5
Rating 14: 4.96
Rating 15: 4.9


In [214]:
#title
import requests
from bs4 import BeautifulSoup
import re

webpage = requests.get('https://www.beeradvocate.com/beer/top-rated/')
soup = BeautifulSoup(webpage.content, 'html.parser')

# Find all anchor tags with matching 'href' using a regular expression
anchor_tags = soup.find_all('a', href=lambda href: href and re.match(r'/beer/profile/\w+/\w+', href))

# Initialize an empty list to store titles
titles_list = []

# Iterate through the anchor tags and append titles to the list
for anchor_tag in anchor_tags:
    # Get the text within the anchor tag and add it to the list
    title_text = anchor_tag.get_text(strip=True)
    titles_list.append(title_text)

# Print the list of extracted titles
print(titles_list)


['Kentucky Brunch Brand Stout', 'Vanilla Bean Assassin', 'Marshmallow Handjee', 'Abraxas - Barrel-Aged', "Hunahpu's Imperial Stout - Double Barrel Aged", 'Blessed', 'Heady Topper', 'O.W.K.', "Mornin' Delight", 'King Julius', 'A Deal With The Devil - Triple Oak-Aged', 'King JJJuliusss', 'Zenne Y Frontera', 'Pliny The Younger', 'Coconut Vibes - Barrel-Aged', 'Barrel Aged Imperial German Chocolate Cupcake Stout', 'Fundamental Observation', 'Very Hazy', 'Bourbon County Brand Coffee Stout', 'V.S.O.J.', 'Oude Fermier', 'A Deal With The Devil - Double Oak-Aged', 'Clover', 'Anabasis', 'Chemtrailmix - Rye Barrel', 'Double Barrel V.S.O.J.', 'Julius', "Fou' Foune", 'Monster Tones', 'Very Green', 'Assassin', 'Juice Machine', 'Very GGGreennn', 'Westly', 'It Was All A Dream', 'Pliny The Elder', 'CBS (Canadian Breakfast Stout)', 'Samuel', 'Abner', 'Framboise Du Fermier', 'Double Sunshine', 'JJJuliusss!', 'Speedway Stout - Vietnamese Coffee - Bourbon-Barrel Aged', 'Dinner', 'Duck Duck Gooze', 'Lou Pep

In [215]:
#reviews
import requests
from bs4 import BeautifulSoup

# Define the base URL
base_url = 'https://www.beeradvocate.com/beer/top-rated/'

# Send a request to the base URL and parse the content
webpage = requests.get(base_url)
soup = BeautifulSoup(webpage.content, 'html.parser')

# Find all anchor tags with 'href' containing '/beer/profile/'
anchor_tags = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)

# Create an empty list to store the extracted text
extracted_text_list = []

# Iterate through the links and extract desired information
for anchor_tag in anchor_tags:
    link = anchor_tag.get('href')
    product_list_url = 'https://www.beeradvocate.com' + link

    # Send a request to the linked page and parse the content
    new_webpage = requests.get(product_list_url)
    new_soup = BeautifulSoup(new_webpage.content, 'html.parser')

    # Find the div with the specified style attribute
    div_with_text = new_soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')

    # Extract and append the desired text to the list
    desired_text = [div.get_text(strip=True) for div in div_with_text]
    extracted_text_list.extend(desired_text)

# Print or do further processing with the extracted_text_list
for text in extracted_text_list:
    print(text)


Amazing stout, expensive but worth the price!
This beer meet and exceeded all the unreal hype. It is simply amazing!
Let it sit and warm to the room a little ... unbelievable.
A small pour, ebony dark, no real head. Intense, rich aroma, brownies and German chocolate cake; dark sweetness. The taste amplifies the smell with the addition of sublime Kentucky bourbon. Heavy body; dense, chewy residual sugar feel with a sublime whiskey heat.This beauty was generously provided by @azuelke (Adam) at a bottle share hosted by @GreenBayBA in Sheboygan, WI. There were many great beers sample, many beautiful and exquisite dark beers, but nothing quite like this legendary beer. If ever you have a chance to try this one, all I can say is don't pass it up. The beer lives up to its legendary status.Pouring temperature: n/a; bottling info: unknown year, bottle number #138Source: @azuelke (Adam), Sheboygan, WI bottle share
Vintage 2022, served on tap at Toppling Goliath in a "snulip" glass. Opaque deep b

In [217]:
import requests
from bs4 import BeautifulSoup
import re

# Define the base URL
base_url = 'https://www.beeradvocate.com/beer/top-rated/'

# Send a request to the base URL and parse the content
webpage = requests.get(base_url)
soup = BeautifulSoup(webpage.content, 'html.parser')

# Find all anchor tags with 'href' containing '/beer/profile/'
anchor_tags = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)

# Create an empty list to store the extracted text and ratings
data_list = []

# Iterate through the links and extract desired information
for anchor_tag in anchor_tags:
    link = anchor_tag.get('href')
    product_list_url = 'https://www.beeradvocate.com' + link

    # Send a request to the linked page and parse the content
    new_webpage = requests.get(product_list_url)
    new_soup = BeautifulSoup(new_webpage.content, 'html.parser')

    # Find all elements with the specified class for ratings
    rating_divs_muted = new_soup.find_all('span', class_='muted')
    rating_divs_BAscore_norm = new_soup.find_all('span', class_='BAscore_norm')

    # Define the regular expression patterns to extract ratings
    pattern_decimal = r'<b>(\d+\.\d+)</b>'
    pattern_integer = r'<b>(\d+)</b>'
    pattern_decimal_BAscore_norm = r'<span class="BAscore_norm">(\d+\.\d+)</span>'
    pattern_integer_BAscore_norm = r'<span class="BAscore_norm">(\d+)</span>'

    # Initialize a dictionary to store the extracted data
    extracted_data = {}

    # Extract and append the desired text to the dictionary
    div_with_text = new_soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')
    desired_text = [div.get_text(strip=True) for div in div_with_text]
    extracted_data['text'] = desired_text

    # Extract ratings using re.findall and append them to the dictionary
    ratings_list = []

    for rating_div in rating_divs_muted:
        ratings_decimal = re.findall(pattern_decimal, str(rating_div))
        ratings_integer = re.findall(pattern_integer, str(rating_div))
        ratings_list.extend(ratings_decimal)
        ratings_list.extend(ratings_integer)

    for rating_div in rating_divs_BAscore_norm:
        ratings_decimal = re.findall(pattern_decimal_BAscore_norm, str(rating_div))
        ratings_integer = re.findall(pattern_integer_BAscore_norm, str(rating_div))
        ratings_list.extend(ratings_decimal)
        ratings_list.extend(ratings_integer)

    extracted_data['ratings'] = ratings_list

    # Append the dictionary to the data list
    data_list.append(extracted_data)

# Print or do further processing with the data_list
for i, data in enumerate(data_list, start=1):
    print(f"Entry {i}:")
    print("Text:", data['text'])
    print("Ratings:", data['ratings'])
    print()


Entry 1:
Text: ['Amazing stout, expensive but worth the price!', 'This beer meet and exceeded all the unreal hype. It is simply amazing!', 'Let it sit and warm to the room a little ... unbelievable.', "A small pour, ebony dark, no real head. Intense, rich aroma, brownies and German chocolate cake; dark sweetness. The taste amplifies the smell with the addition of sublime Kentucky bourbon. Heavy body; dense, chewy residual sugar feel with a sublime whiskey heat.This beauty was generously provided by @azuelke (Adam) at a bottle share hosted by @GreenBayBA in Sheboygan, WI. There were many great beers sample, many beautiful and exquisite dark beers, but nothing quite like this legendary beer. If ever you have a chance to try this one, all I can say is don't pass it up. The beer lives up to its legendary status.Pouring temperature: n/a; bottling info: unknown year, bottle number #138Source: @azuelke (Adam), Sheboygan, WI bottle share", 'Vintage 2022, served on tap at Toppling Goliath in a 

In [219]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd

# Define the base URL
base_url = 'https://www.beeradvocate.com/beer/top-rated/'

# Send a request to the base URL and parse the content
webpage = requests.get(base_url)
soup = BeautifulSoup(webpage.content, 'html.parser')

# Find all anchor tags with 'href' containing '/beer/profile/'
anchor_tags = soup.find_all('a', href=lambda href: href and '/beer/profile/' in href)

# Create an empty list to store the extracted data
data_list = []

# Iterate through the links and extract desired information
for anchor_tag in anchor_tags:
    link = anchor_tag.get('href')
    product_list_url = 'https://www.beeradvocate.com' + link

    # Send a request to the linked page and parse the content
    new_webpage = requests.get(product_list_url)
    new_soup = BeautifulSoup(new_webpage.content, 'html.parser')

    # Find all elements with the specified class for ratings
    rating_divs_muted = new_soup.find_all('span', class_='muted')
    rating_divs_BAscore_norm = new_soup.find_all('span', class_='BAscore_norm')

    # Define the regular expression patterns to extract ratings
    pattern_decimal = r'<b>(\d+\.\d+)</b>'
    pattern_integer = r'<b>(\d+)</b>'
    pattern_decimal_BAscore_norm = r'<span class="BAscore_norm">(\d+\.\d+)</span>'
    pattern_integer_BAscore_norm = r'<span class="BAscore_norm">(\d+)</span>'

    # Initialize a dictionary to store the extracted data
    extracted_data = {}

    # Extract and append the desired text to the dictionary
    div_with_text = new_soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')
    desired_text = [div.get_text(strip=True) for div in div_with_text]
    extracted_data['text'] = ' '.join(desired_text)

    # Extract ratings using re.findall and append them to the dictionary
    ratings_list = []

    for rating_div in rating_divs_muted:
        ratings_decimal = re.findall(pattern_decimal, str(rating_div))
        ratings_integer = re.findall(pattern_integer, str(rating_div))
        ratings_list.extend(ratings_decimal)
        ratings_list.extend(ratings_integer)

    for rating_div in rating_divs_BAscore_norm:
        ratings_decimal = re.findall(pattern_decimal_BAscore_norm, str(rating_div))
        ratings_integer = re.findall(pattern_integer_BAscore_norm, str(rating_div))
        ratings_list.extend(ratings_decimal)
        ratings_list.extend(ratings_integer)

    extracted_data['ratings'] = ', '.join(ratings_list)

    # Append the dictionary to the data list
    data_list.append(extracted_data)

# Create a DataFrame from the data_list
df = pd.DataFrame(data_list)

# Print the DataFrame or perform further processing as needed
df


text  \
0    Amazing stout, expensive but worth the price! ...   
1                                                        
2    12oz bottle…2022 version. Drank 12/25/22.Pours...   
3                                                        
4    09/11/23 draft @ Winking Lizard Canton 2022 vi...   
..                                                 ...   
495                                                      
496  2014 bottle.Stickee Monkee is a Belgian-style ...   
497                                                      
498  2017 vintage - shared with me from a friend. S...   
499                                                      

                                               ratings  
0    4.75, 4.52, 5, 5, 4.96, 4.5, 4.75, 4.75, 5, 4....  
1                                                       
2    5, 4.81, 5, 5, 4.98, 4.27, 4.4, 4.93, 4.96, 4....  
3                                                       
4    4.71, 4.75, 4.75, 5, 4.53, 4.44, 5, 4.84, 4.28...  
..                                                 ...  
495                                                     
496  4.15, 4.59, 4.1, 3.75, 5, 4.46, 4.44, 4.43, 4....  
497                                                     
498  4, 4.92, 4.46, 5, 4.5, 4.16, 4.67, 3.99, 4.6, ...  
499                                                     

[500 rows x 2 columns]

# Final Code!

In [222]:
import requests
from bs4 import BeautifulSoup
import re
import pandas as pd

# Define the base URL
base_url = 'https://www.beeradvocate.com/beer/top-rated/'

# Send a request to the base URL and parse the content
webpage = requests.get(base_url)
soup = BeautifulSoup(webpage.content, 'html.parser')

# Find all anchor tags with matching 'href' using a regular expression
anchor_tags = soup.find_all('a', href=lambda href: href and re.match(r'/beer/profile/\w+/\w+', href))

# Initialize an empty list to store titles
titles_list = []

# Iterate through the anchor tags and append titles to the list
for anchor_tag in anchor_tags:
    # Get the text within the anchor tag and add it to the list
    title_text = anchor_tag.get_text(strip=True)
    titles_list.append(title_text)

# Create a DataFrame with titles
title_df = pd.DataFrame({'Title': titles_list})

# Create an empty list to store the extracted data
data_list = []

# Iterate through the links and extract desired information
for anchor_tag in anchor_tags:
    link = anchor_tag.get('href')
    product_list_url = 'https://www.beeradvocate.com' + link

    # Send a request to the linked page and parse the content
    new_webpage = requests.get(product_list_url)
    new_soup = BeautifulSoup(new_webpage.content, 'html.parser')

    # Find all elements with the specified class for ratings
    rating_divs_muted = new_soup.find_all('span', class_='muted')
    rating_divs_BAscore_norm = new_soup.find_all('span', class_='BAscore_norm')

    # Define the regular expression patterns to extract ratings
    pattern_decimal = r'<b>(\d+\.\d+)</b>'
    pattern_integer = r'<b>(\d+)</b>'
    pattern_decimal_BAscore_norm = r'<span class="BAscore_norm">(\d+\.\d+)</span>'
    pattern_integer_BAscore_norm = r'<span class="BAscore_norm">(\d+)</span>'

    # Initialize a dictionary to store the extracted data
    extracted_data = {}

    # Extract the desired text without joining them
    div_with_text = new_soup.find_all('div', style='margin:20px 0px; font-size:11pt; line-height:1.4;')
    extracted_data['text'] = [div.get_text(strip=True) for div in div_with_text]

    # Extract ratings using re.findall and append them to the dictionary
    ratings_list = []

    for rating_div in rating_divs_muted:
        ratings_decimal = re.findall(pattern_decimal, str(rating_div))
        ratings_integer = re.findall(pattern_integer, str(rating_div))
        ratings_list.extend(ratings_decimal)
        ratings_list.extend(ratings_integer)

    for rating_div in rating_divs_BAscore_norm:
        ratings_decimal = re.findall(pattern_decimal_BAscore_norm, str(rating_div))
        ratings_integer = re.findall(pattern_integer_BAscore_norm, str(rating_div))
        ratings_list.extend(ratings_decimal)
        ratings_list.extend(ratings_integer)

    extracted_data['ratings'] = ratings_list

    # Append the dictionary to the data list
    data_list.append(extracted_data)

# Create a DataFrame from the data_list
data_df = pd.DataFrame(data_list)

# Combine the title DataFrame and data DataFrame
result_df = pd.concat([title_df, data_df], axis=1)

# Print or do further processing with the result_df
result_df


Title  \
0                      Kentucky Brunch Brand Stout   
1                            Vanilla Bean Assassin   
2                              Marshmallow Handjee   
3                            Abraxas - Barrel-Aged   
4    Hunahpu's Imperial Stout - Double Barrel Aged   
..                                             ...   
245                                      The Abyss   
246          All That Is And All That Ever Will Be   
247                                        Abraxas   
248                                 Stickee Monkee   
249                           Samuel Adams Utopias   

                                                  text  \
0    [Amazing stout, expensive but worth the price!...   
1    [12oz bottle…2022 version. Drank 12/25/22.Pour...   
2    [09/11/23 draft @ Winking Lizard Canton, 2022 ...   
3    l waxed and capped bottle into a DDG teku...   
4    [LONG time want of mine! 2016 vintage. Unfortu...   
..                                                 ...   
245  [L - Look is black like coffee bu with little ...   
246  [Pours a deep dark almost black color with a f...   
247  [Pours an opaque, pitch-black coloration with ...   
248  [2014 bottle.Stickee Monkee is a Belgian-style...   
249  [2017 vintage - shared with me from a friend. ...   

                                               ratings  
0    [4.75, 4.52, 5, 5, 4.96, 4.5, 4.75, 4.75, 5, 4...  
1    [5, 4.81, 5, 5, 4.98, 4.27, 4.4, 4.93, 4.96, 4...  
2    [4.71, 4.75, 4.75, 5, 4.53, 4.44, 5, 4.84, 4.2...  
3    [4.19, 4.84, 4.83, 4.64, 4.53, 4.59, 4.59, 4.4...  
4    [4.51, 3.68, 4.48, 4.27, 5, 4.77, 4.75, 4.75, ...  
..                                                 ...  
245  [4.23, 4.91, 5, 4.5, 4.22, 4.5, 4.45, 4.2, 4.7...  
246  [4.19, 5, 4.6, 4.54, 4.18, 4.05, 4.17, 4.45, 4...  
247  [4.5, 4.44, 4.5, 4.75, 4.68, 4.08, 4.5, 4.4, 4...  
248  [4.15, 4.59, 4.1, 3.75, 5, 4.46, 4.44, 4.43, 4...  
249  [4, 4.92, 4.46, 5, 4.5, 4.16, 4.67, 3.99, 4.6,...  

[250 rows x 3 columns]

['Amazing stout, expensive but worth the price!',
 'This beer meet and exceeded all the unreal hype. It is simply amazing!',
 'Let it sit and warm to the room a little ... unbelievable.',
 "A small pour, ebony dark, no real head. Intense, rich aroma, brownies and German chocolate cake; dark sweetness. The taste amplifies the smell with the addition of sublime Kentucky bourbon. Heavy body; dense, chewy residual sugar feel with a sublime whiskey heat.This beauty was generously provided by @azuelke (Adam) at a bottle share hosted by @GreenBayBA in Sheboygan, WI. There were many great beers sample, many beautiful and exquisite dark beers, but nothing quite like this legendary beer. If ever you have a chance to try this one, all I can say is don't pass it up. The beer lives up to its legendary status.Pouring temperature: n/a; bottling info: unknown year, bottle number #138Source: @azuelke (Adam), Sheboygan, WI bottle share",
 'Vintage 2022, served on tap at Toppling Goliath in a "snulip" gl